# install packages into venv, cs-5420

In [13]:
import sys 
!conda install --yes --prefix {sys.prefix} geojson

Solving environment: failed with initial frozen solve. Retrying with flexible solve.
Solving environment: / 
  - conda-forge/noarch::packaging-21.2-pyhd8ed1ab_1, conda-forge/noarch::pyparsing-2.4.7-pyhd8ed1ab_1
  - conda-forge/noarch::packaging-21.0-pyhd8ed1ab_0, conda-forge/noarch::pyparsing-3.0.3-pyhd8ed1abdone
Solving environment: failed with initial frozen solve. Retrying with flexible solve.
Solving environment: done

## Package Plan ##

  environment location: /opt/anaconda3/envs/cs-5420

  added / updated specs:
    - geojson


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    anyio-3.3.4                |   py39h6e9494a_0         148 KB  conda-forge
    appnope-0.1.2              |   py39h6e9494a_1          10 KB  conda-forge
    argon2-cffi-21.1.0         |   py39h89e85a6_0          44 KB  conda-forge
    async_generator-1.10       |             py_0          18 KB  conda-forge
   

webencodings-0.5.1   | 12 KB     | ##################################### | 100% 
attrs-21.2.0         | 44 KB     | ##################################### | 100% 
backports-1.0        | 4 KB      | ##################################### | 100% 
jupyter_client-7.0.6 | 87 KB     | ##################################### | 100% 
six-1.16.0           | 14 KB     | ##################################### | 100% 
sqlite-3.36.0        | 1.8 MB    | ##################################### | 100% 
zipp-3.6.0           | 12 KB     | ##################################### | 100% 
bzip2-1.0.8          | 155 KB    | ##################################### | 100% 
pandocfilters-1.5.0  | 11 KB     | ##################################### | 100% 
send2trash-1.8.0     | 17 KB     | ##################################### | 100% 
nbconvert-6.2.0      | 556 KB    | ##################################### | 100% 
json5-0.9.5          | 20 KB     | ##################################### | 100% 
pexpect-4.8.0        | 47 KB

In [164]:
import csv
import time
import geojson
import json
import datetime
import mapbox.services.geocoding as gc

from collections import defaultdict

# load county data

In [165]:
with open('US-Counties.geojson.json') as f:
    county_boundaries = geojson.load(f)
f.close()
features_county_boundaries = county_boundaries['features']


# indices from the air quality csv that will be used for the integration along with states' names

In [166]:
AQI_LAT_INDEX = 0
AQI_LONG_INDEX = 1
AQI_POLLUTNT_INDEX = 3
AQI_INDEX = 4

STATES = ["Alabama", "Alaska", "American Samoa", "Arizona", "Arkansas", "California", 
          "Colorado", "Connecticut", "Delaware", "District of Columbia", "Florida", 
          "Georgia", "Guam", "Hawaii", "Idaho", "Illinois", "Indiana", "Iowa", "Kansas", 
          "Kentucky", "Louisiana", "Maine", "Maryland", "Massachusetts", "Michigan", 
          "Minnesota", "Minor Outlying Islands", "Mississippi", "Missouri", "Montana", 
          "Nebraska", "Nevada", "New Hampshire", "New Jersey", "New Mexico", "New York", 
          "North Carolina", "North Dakota", "Northern Mariana Islands", "Ohio", "Oklahoma", 
          "Oregon", "Pennsylvania", "Puerto Rico", "Rhode Island", "South Carolina", 
          "South Dakota", "Tennessee", "Texas", "U.S. Virgin Islands", "Utah", "Vermont", 
          "Virginia", "Washington", "West Virginia", "Wisconsin", "Wyoming"]

STATES = [s.upper() for s in STATES]
STATES[:2]

['ALABAMA', 'ALASKA']

# load air quality data and extract county info

In [171]:
def is_county(hier):
    if 'COUNTY' in hier:
        return True
    return False

def is_state(hier):
    if hier in STATES:
        return True
    return False

In [173]:
with open('NorthAmerica.csv', newline='') as csvfile:
    aqi_data = csvfile.readlines()
csvfile.close()
print(aqi_data[:1])
print(aqi_data[1].split(","))
len_aqi_data = len(aqi_data)
geo = gc.Geocoder(access_token = 'pk.eyJ1IjoicGRhbmdhbCIsImEiOiJja3RtMDkzejUyMHgyMnhwOGltbmJ2dGI1In0.SDzAt6moKJnqJx_w94KuLw')
   

['"Latitude","Longitude","UTC","Pollutant","AQI","Category","Location","ReportingAgency","StationID","FullStationID"\r\n']
['"38.89"', '"-121.3"', '"2021-10-20T20:00"', '"PM2.5"', '"9"', '"1"', '"Lincoln"', '"Placer County APCD"', '"060612001"', '"840060612001"\r\n']


In [174]:
seen_counties = defaultdict(float)
for i in range(1, len_aqi_data):
    if i % 550 == 0:
        time.sleep(75)
    aqi_lat = float(aqi_data[i].split(",")[AQI_LAT_INDEX].strip("\""))
    aqi_long = float(aqi_data[i].split(",")[AQI_LONG_INDEX].strip("\""))
    aqi_pollutnt = "".join(aqi_data[i].split(",")[AQI_INDEX].strip("\""))
    aqi = float(aqi_data[i].split(",")[AQI_INDEX].strip("\""))
    loc = geo.reverse(aqi_long, aqi_lat)
    loc = loc.geojson()
    features = loc["features"]
    l = len(features)
    
    for i in range(l):

        feature = features[i]
        hier = feature["text"].upper().strip()
        print(datetime.datetime.now(), end="")
        print(f" text value: {hier}")
        if is_county(hier):
            county = hier
            
        if is_state(hier):
            state = hier
    if state and county:       
        seen_counties[county + ',' + state] = aqi
    
    print(seen_counties)
    print()
    print()

with open('county_to_aqi.json', 'w') as f:
    json.dump(seen_counties, f)
f.close()

2021-10-31 09:05:23.325725 text value: M STREET
2021-10-31 09:05:23.326048 text value: 95648
2021-10-31 09:05:23.326124 text value: LINCOLN
2021-10-31 09:05:23.326194 text value: PLACER COUNTY
2021-10-31 09:05:23.326271 text value: CALIFORNIA
2021-10-31 09:05:23.326341 text value: UNITED STATES
defaultdict(<class 'float'>, {'PLACER COUNTY,CALIFORNIA': 9.0})


2021-10-31 09:05:23.340987 text value: DOGWOOD STREET
2021-10-31 09:05:23.341530 text value: V9W 2Y5
2021-10-31 09:05:23.341624 text value: CAMPBELL RIVER
2021-10-31 09:05:23.341686 text value: STRATHCONA REGIONAL DISTRICT
2021-10-31 09:05:23.341744 text value: BRITISH COLUMBIA
2021-10-31 09:05:23.341816 text value: CANADA
defaultdict(<class 'float'>, {'PLACER COUNTY,CALIFORNIA': 33.0})


2021-10-31 09:05:23.355727 text value: HELEN STREET
2021-10-31 09:05:23.355932 text value: V9Y 5P4
2021-10-31 09:05:23.356000 text value: PORT ALBERNI
2021-10-31 09:05:23.356067 text value: ALBERNI-CLAYOQUOT REGIONAL DISTRICT
2021-10-31 09:05:23.

2021-10-31 09:05:23.746990 text value: BUCKLEY AVENUE
2021-10-31 09:05:23.747290 text value: V8B 0J8
2021-10-31 09:05:23.747367 text value: SQUAMISH
2021-10-31 09:05:23.747390 text value: SQUAMISH-LILLOOET REGIONAL DISTRICT
2021-10-31 09:05:23.747419 text value: BRITISH COLUMBIA
2021-10-31 09:05:23.747444 text value: CANADA
defaultdict(<class 'float'>, {'PLACER COUNTY,CALIFORNIA': 57.0, 'CLALLAM COUNTY,WASHINGTON': 31.0, 'CURRY COUNTY,OREGON': 28.0, 'COOS COUNTY,OREGON': 44.0, 'HUMBOLDT COUNTY,CALIFORNIA': 9.0, 'LANE COUNTY,OREGON': 33.0, 'GRAYS HARBOR COUNTY,WASHINGTON': 14.0, 'TILLAMOOK COUNTY,OREGON': 59.0, 'MENDOCINO COUNTY,CALIFORNIA': 27.0, 'PACIFIC COUNTY,WASHINGTON': 50.0, 'JOSEPHINE COUNTY,OREGON': 10.0, 'DOUGLAS COUNTY,OREGON': 44.0, 'POLK COUNTY,OREGON': 7.0, 'BENTON COUNTY,OREGON': 13.0})


2021-10-31 09:05:23.760183 text value: FIGUEROA STREET
2021-10-31 09:05:23.760276 text value: BETHEL-DANEBO
2021-10-31 09:05:23.760301 text value: 97402
2021-10-31 09:05:23.760325 text v

2021-10-31 09:05:23.962823 text value: KENSINGTON OUTDOOR POOL
2021-10-31 09:05:23.963013 text value: PARKCREST - AUBREY
2021-10-31 09:05:23.963069 text value: V5B 2A2
2021-10-31 09:05:23.963126 text value: BURNABY
2021-10-31 09:05:23.963180 text value: METRO VANCOUVER
2021-10-31 09:05:23.963233 text value: BRITISH COLUMBIA
2021-10-31 09:05:23.963286 text value: CANADA
defaultdict(<class 'float'>, {'PLACER COUNTY,CALIFORNIA': 57.0, 'CLALLAM COUNTY,WASHINGTON': 31.0, 'CURRY COUNTY,OREGON': 28.0, 'COOS COUNTY,OREGON': 44.0, 'HUMBOLDT COUNTY,CALIFORNIA': 9.0, 'LANE COUNTY,OREGON': 12.0, 'GRAYS HARBOR COUNTY,WASHINGTON': 14.0, 'TILLAMOOK COUNTY,OREGON': 59.0, 'MENDOCINO COUNTY,CALIFORNIA': 27.0, 'PACIFIC COUNTY,WASHINGTON': 50.0, 'JOSEPHINE COUNTY,OREGON': 10.0, 'DOUGLAS COUNTY,OREGON': 44.0, 'POLK COUNTY,OREGON': 7.0, 'BENTON COUNTY,OREGON': 13.0, 'WASHINGTON COUNTY,OREGON': 66.0, 'MASON COUNTY,WASHINGTON': 22.0, 'LINN COUNTY,OREGON': 8.0, 'MARION COUNTY,OREGON': 38.0})


2021-10-31 09:05

2021-10-31 09:05:24.179194 text value: PONDEROSA STREET
2021-10-31 09:05:24.179411 text value: 97539
2021-10-31 09:05:24.179462 text value: SHADY COVE
2021-10-31 09:05:24.179512 text value: JACKSON COUNTY
2021-10-31 09:05:24.179566 text value: OREGON
2021-10-31 09:05:24.179625 text value: UNITED STATES
defaultdict(<class 'float'>, {'PLACER COUNTY,CALIFORNIA': 57.0, 'CLALLAM COUNTY,WASHINGTON': 31.0, 'CURRY COUNTY,OREGON': 28.0, 'COOS COUNTY,OREGON': 44.0, 'HUMBOLDT COUNTY,CALIFORNIA': 9.0, 'LANE COUNTY,OREGON': 12.0, 'GRAYS HARBOR COUNTY,WASHINGTON': 14.0, 'TILLAMOOK COUNTY,OREGON': 59.0, 'MENDOCINO COUNTY,CALIFORNIA': 27.0, 'PACIFIC COUNTY,WASHINGTON': 50.0, 'JOSEPHINE COUNTY,OREGON': 10.0, 'DOUGLAS COUNTY,OREGON': 44.0, 'POLK COUNTY,OREGON': 7.0, 'BENTON COUNTY,OREGON': 13.0, 'WASHINGTON COUNTY,OREGON': 8.0, 'MASON COUNTY,WASHINGTON': 22.0, 'LINN COUNTY,OREGON': 8.0, 'MARION COUNTY,OREGON': 38.0, 'LEWIS COUNTY,WASHINGTON': 15.0, 'COWLITZ COUNTY,WASHINGTON': 23.0, 'JACKSON COUNTY,OREG

2021-10-31 09:05:24.393280 text value: SOUTH FOOTHILL DRIVE
2021-10-31 09:05:24.393427 text value: 96097
2021-10-31 09:05:24.393512 text value: YREKA
2021-10-31 09:05:24.393564 text value: SISKIYOU COUNTY
2021-10-31 09:05:24.393607 text value: CALIFORNIA
2021-10-31 09:05:24.393651 text value: UNITED STATES
defaultdict(<class 'float'>, {'PLACER COUNTY,CALIFORNIA': 57.0, 'CLALLAM COUNTY,WASHINGTON': 31.0, 'CURRY COUNTY,OREGON': 28.0, 'COOS COUNTY,OREGON': 44.0, 'HUMBOLDT COUNTY,CALIFORNIA': 9.0, 'LANE COUNTY,OREGON': 12.0, 'GRAYS HARBOR COUNTY,WASHINGTON': 14.0, 'TILLAMOOK COUNTY,OREGON': 59.0, 'MENDOCINO COUNTY,CALIFORNIA': 27.0, 'PACIFIC COUNTY,WASHINGTON': 50.0, 'JOSEPHINE COUNTY,OREGON': 10.0, 'DOUGLAS COUNTY,OREGON': 44.0, 'POLK COUNTY,OREGON': 7.0, 'BENTON COUNTY,OREGON': 13.0, 'WASHINGTON COUNTY,OREGON': 20.0, 'MASON COUNTY,WASHINGTON': 22.0, 'LINN COUNTY,OREGON': 11.0, 'MARION COUNTY,OREGON': 14.0, 'LEWIS COUNTY,WASHINGTON': 15.0, 'COWLITZ COUNTY,WASHINGTON': 23.0, 'JACKSON COUNT

...

2021-10-31 09:08:09.843154 text value: SAINT NICHOLAS TERRACE
2021-10-31 09:08:09.843617 text value: HAMILTON HEIGHTS
2021-10-31 09:08:09.843739 text value: 10031
2021-10-31 09:08:09.844503 text value: MANHATTAN
2021-10-31 09:08:09.844627 text value: NEW YORK
2021-10-31 09:08:09.844749 text value: NEW YORK COUNTY
2021-10-31 09:08:09.844867 text value: NEW YORK
2021-10-31 09:08:09.845011 text value: UNITED STATES
defaultdict(<class 'float'>, {'PLACER COUNTY,CALIFORNIA': 22.0, 'CLALLAM COUNTY,WASHINGTON': 31.0, 'CURRY COUNTY,OREGON': 28.0, 'COOS COUNTY,OREGON': 44.0, 'HUMBOLDT COUNTY,CALIFORNIA': 9.0, 'LANE COUNTY,OREGON': 17.0, 'GRAYS HARBOR COUNTY,WASHINGTON': 14.0, 'TILLAMOOK COUNTY,OREGON': 59.0, 'MENDOCINO COUNTY,CALIFORNIA': 27.0, 'PACIFIC COUNTY,WASHINGTON': 50.0, 'JOSEPHINE COUNTY,OREGON': 10.0, 'DOUGLAS COUNTY,OREGON': 44.0, 'POLK COUNTY,OREGON': 7.0, 'BENTON COUNTY,OREGON': 13.0, 'WASHINGTON COUNTY,OREGON': 20.0, 'MASON COUNTY,WASHINGTON': 22.0, 'LINN COUNTY,OREGON': 15.0, 'MAR

2021-10-31 09:08:10.050396 text value: CHEMIN DUNCAN
2021-10-31 09:08:10.050684 text value: H4P 2A2
2021-10-31 09:08:10.050751 text value: MONT-ROYAL
2021-10-31 09:08:10.050804 text value: QUEBEC
2021-10-31 09:08:10.050880 text value: CANADA
defaultdict(<class 'float'>, {'PLACER COUNTY,CALIFORNIA': 22.0, 'CLALLAM COUNTY,WASHINGTON': 31.0, 'CURRY COUNTY,OREGON': 28.0, 'COOS COUNTY,OREGON': 44.0, 'HUMBOLDT COUNTY,CALIFORNIA': 9.0, 'LANE COUNTY,OREGON': 17.0, 'GRAYS HARBOR COUNTY,WASHINGTON': 14.0, 'TILLAMOOK COUNTY,OREGON': 59.0, 'MENDOCINO COUNTY,CALIFORNIA': 27.0, 'PACIFIC COUNTY,WASHINGTON': 50.0, 'JOSEPHINE COUNTY,OREGON': 10.0, 'DOUGLAS COUNTY,OREGON': 44.0, 'POLK COUNTY,OREGON': 7.0, 'BENTON COUNTY,OREGON': 13.0, 'WASHINGTON COUNTY,OREGON': 20.0, 'MASON COUNTY,WASHINGTON': 22.0, 'LINN COUNTY,OREGON': 15.0, 'MARION COUNTY,OREGON': 15.0, 'LEWIS COUNTY,WASHINGTON': 15.0, 'COWLITZ COUNTY,WASHINGTON': 23.0, 'JACKSON COUNTY,OREGON': 27.0, 'THURSTON COUNTY,WASHINGTON': 9.0, 'SONOMA COUNTY

2021-10-31 09:08:10.272157 text value: 7TH AVENUE
2021-10-31 09:08:10.272338 text value: GERMANTOWN
2021-10-31 09:08:10.272394 text value: 06810
2021-10-31 09:08:10.272443 text value: DANBURY
2021-10-31 09:08:10.272492 text value: FAIRFIELD COUNTY
2021-10-31 09:08:10.272541 text value: CONNECTICUT
2021-10-31 09:08:10.273279 text value: UNITED STATES
defaultdict(<class 'float'>, {'PLACER COUNTY,CALIFORNIA': 22.0, 'CLALLAM COUNTY,WASHINGTON': 31.0, 'CURRY COUNTY,OREGON': 28.0, 'COOS COUNTY,OREGON': 44.0, 'HUMBOLDT COUNTY,CALIFORNIA': 9.0, 'LANE COUNTY,OREGON': 17.0, 'GRAYS HARBOR COUNTY,WASHINGTON': 14.0, 'TILLAMOOK COUNTY,OREGON': 59.0, 'MENDOCINO COUNTY,CALIFORNIA': 27.0, 'PACIFIC COUNTY,WASHINGTON': 50.0, 'JOSEPHINE COUNTY,OREGON': 10.0, 'DOUGLAS COUNTY,OREGON': 44.0, 'POLK COUNTY,OREGON': 7.0, 'BENTON COUNTY,OREGON': 13.0, 'WASHINGTON COUNTY,OREGON': 20.0, 'MASON COUNTY,WASHINGTON': 22.0, 'LINN COUNTY,OREGON': 15.0, 'MARION COUNTY,OREGON': 15.0, 'LEWIS COUNTY,WASHINGTON': 15.0, 'COWL

2021-10-31 09:08:10.481576 text value: 2 S RANG
2021-10-31 09:08:10.481682 text value: G0X 1E0
2021-10-31 09:08:10.481735 text value: CHARETTE
2021-10-31 09:08:10.481786 text value: MASKINONGÉ REGIONAL COUNTY MUNICIPALITY
2021-10-31 09:08:10.481836 text value: QUEBEC
2021-10-31 09:08:10.481884 text value: CANADA
defaultdict(<class 'float'>, {'PLACER COUNTY,CALIFORNIA': 22.0, 'CLALLAM COUNTY,WASHINGTON': 31.0, 'CURRY COUNTY,OREGON': 28.0, 'COOS COUNTY,OREGON': 44.0, 'HUMBOLDT COUNTY,CALIFORNIA': 9.0, 'LANE COUNTY,OREGON': 17.0, 'GRAYS HARBOR COUNTY,WASHINGTON': 14.0, 'TILLAMOOK COUNTY,OREGON': 59.0, 'MENDOCINO COUNTY,CALIFORNIA': 27.0, 'PACIFIC COUNTY,WASHINGTON': 50.0, 'JOSEPHINE COUNTY,OREGON': 10.0, 'DOUGLAS COUNTY,OREGON': 44.0, 'POLK COUNTY,OREGON': 7.0, 'BENTON COUNTY,OREGON': 13.0, 'WASHINGTON COUNTY,OREGON': 20.0, 'MASON COUNTY,WASHINGTON': 22.0, 'LINN COUNTY,OREGON': 15.0, 'MARION COUNTY,OREGON': 15.0, 'LEWIS COUNTY,WASHINGTON': 15.0, 'COWLITZ COUNTY,WASHINGTON': 23.0, 'JACKSON

2021-10-31 09:08:10.691126 text value: SMITH STREET
2021-10-31 09:08:10.691243 text value: 06340
2021-10-31 09:08:10.691294 text value: GROTON
2021-10-31 09:08:10.691336 text value: NEW LONDON COUNTY
2021-10-31 09:08:10.691378 text value: CONNECTICUT
2021-10-31 09:08:10.691421 text value: UNITED STATES
defaultdict(<class 'float'>, {'PLACER COUNTY,CALIFORNIA': 22.0, 'CLALLAM COUNTY,WASHINGTON': 31.0, 'CURRY COUNTY,OREGON': 28.0, 'COOS COUNTY,OREGON': 44.0, 'HUMBOLDT COUNTY,CALIFORNIA': 9.0, 'LANE COUNTY,OREGON': 17.0, 'GRAYS HARBOR COUNTY,WASHINGTON': 14.0, 'TILLAMOOK COUNTY,OREGON': 59.0, 'MENDOCINO COUNTY,CALIFORNIA': 27.0, 'PACIFIC COUNTY,WASHINGTON': 50.0, 'JOSEPHINE COUNTY,OREGON': 10.0, 'DOUGLAS COUNTY,OREGON': 44.0, 'POLK COUNTY,OREGON': 7.0, 'BENTON COUNTY,OREGON': 13.0, 'WASHINGTON COUNTY,OREGON': 20.0, 'MASON COUNTY,WASHINGTON': 22.0, 'LINN COUNTY,OREGON': 15.0, 'MARION COUNTY,OREGON': 15.0, 'LEWIS COUNTY,WASHINGTON': 15.0, 'COWLITZ COUNTY,WASHINGTON': 23.0, 'JACKSON COUNTY,OR

In [60]:
print(f"total rows in counties: {len(features_county_boundaries)}\ntotal rows in aqi data: {len(aqi_data)}")

total rows in counties: 3221
total rows in aqi data: 1161


# aqi goes into the property field in county data

# getting used to the geocoding api for mapbox below

In [ ]:
# read the tuples from 

In [45]:
l = len(aqi_data)
for i in range(l):
    # dict from county to list of coordinates
for i in range(3221):
    feature = features_county_boundaries[i]
    candidate_locs = feature["geometry"]["coordinates"]
    l = len(candidate_locs)
    candidate_locs = candidate_locs[(l // 2 - l // 4) : (l // 2 + l // 4)]
    county_name = gc.reverse()
    

SyntaxError: f-string: unmatched '[' (3872160820.py, line 1)

In [44]:
features_county_boundaries[0]["properties"]

{'GEO_ID': '0500000US01029',
 'STATE': '01',
 'COUNTY': '029',
 'NAME': 'Cleburne',
 'LSAD': 'County',
 'CENSUSAREA': 560.1}

In [48]:
features_county_boundaries[0]["geometry"]["coordinates"]

[[[-85.388717, 33.913044],
  [-85.380885, 33.873508],
  [-85.379455, 33.866291],
  [-85.377426, 33.856047],
  [-85.376403, 33.850656],
  [-85.364595, 33.788446],
  [-85.361844, 33.773951],
  [-85.360491, 33.767958],
  [-85.357402, 33.750104],
  [-85.355252, 33.739245],
  [-85.344054, 33.682684],
  [-85.342722, 33.675953],
  [-85.323792, 33.580339],
  [-85.31534, 33.537646],
  [-85.314994, 33.535898],
  [-85.314843, 33.534951],
  [-85.314091, 33.530218],
  [-85.313999, 33.529807],
  [-85.304439, 33.482884],
  [-85.308211, 33.481579],
  [-85.30925, 33.483137],
  [-85.314852, 33.487603],
  [-85.316028, 33.488267],
  [-85.320893, 33.488359],
  [-85.324856, 33.489161],
  [-85.331061, 33.491014],
  [-85.33828, 33.4947],
  [-85.342544, 33.495961],
  [-85.344923, 33.497608],
  [-85.346705, 33.501148],
  [-85.349958, 33.501216],
  [-85.351594, 33.4996],
  [-85.354491, 33.498866],
  [-85.352576, 33.494538],
  [-85.352573, 33.492438],
  [-85.355315, 33.49248],
  [-85.497455, 33.494624],
  [-85.50

# a way to print json in a pretty format

In [56]:
print(json.dumps(features_county_boundaries[0], indent=4))
help(json.dumps)

{
    "type": "Feature",
    "geometry": {
        "type": "Polygon",
        "coordinates": [
            [
                [
                    -85.388717,
                    33.913044
                ],
                [
                    -85.380885,
                    33.873508
                ],
                [
                    -85.379455,
                    33.866291
                ],
                [
                    -85.377426,
                    33.856047
                ],
                [
                    -85.376403,
                    33.850656
                ],
                [
                    -85.364595,
                    33.788446
                ],
                [
                    -85.361844,
                    33.773951
                ],
                [
                    -85.360491,
                    33.767958
                ],
                [
                    -85.357402,
                    33.750104
                ],


# using the geocoder for forward and reverse geocoding

In [129]:

geo = gc.Geocoder(access_token = 'pk.eyJ1IjoicGRhbmdhbCIsImEiOiJja3RtMDkzejUyMHgyMnhwOGltbmJ2dGI1In0.SDzAt6moKJnqJx_w94KuLw')
loc = geo.reverse(-87.359296,35.00118)
loc = loc.geojson()
loc

{'type': 'FeatureCollection',
 'query': [-87.3593, 35.00118],
 'features': [{'id': 'address.2383805222255382',
   'type': 'Feature',
   'place_type': ['address'],
   'relevance': 1,
   'properties': {'accuracy': 'street'},
   'text': 'Tennessee Highway 101',
   'place_name': 'Tennessee Highway 101, Five Points, Alabama 35648, United States',
   'center': [-87.3593930557165, 35.00118400445745],
   'geometry': {'type': 'Point',
    'coordinates': [-87.3593930557165, 35.00118400445745]},
   'context': [{'id': 'postcode.5346431396764190', 'text': '35648'},
    {'id': 'place.14184494992927130',
     'wikidata': 'Q5456076',
     'text': 'Five Points'},
    {'id': 'district.1371839929703080',
     'wikidata': 'Q261672',
     'text': 'Lauderdale County'},
    {'id': 'region.11450320215359250',
     'wikidata': 'Q173',
     'short_code': 'US-AL',
     'text': 'Alabama'},
    {'id': 'country.19678805456372290',
     'wikidata': 'Q30',
     'short_code': 'us',
     'text': 'United States'}]},
  {